# Geospatial visualization tutorial - 1

Hi all :-)

This is Yeonjun IN who made the kernel named as [\[DS4C\]time series geospatial eda using folium.](https://www.kaggle.com/mbnb8317/ds4c-time-series-geospatial-eda-using-folium)

This time, I made a Tutorial about Folium, a Package for Geospatial visualization, for novice of EDA.

I hope it helps

Thank you :)

In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)


import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))
        
import seaborn as sns
import matplotlib.pyplot as plt

import folium 
from folium import plugins
# from folium.plugins import HeatMap

import json 
from datetime import datetime

import warnings
warnings.filterwarnings("ignore")

/kaggle/input/novel-corona-virus-2019-dataset/time_series_covid_19_confirmed.csv
/kaggle/input/novel-corona-virus-2019-dataset/time_series_covid_19_confirmed_US.csv
/kaggle/input/novel-corona-virus-2019-dataset/time_series_covid_19_deaths_US.csv
/kaggle/input/novel-corona-virus-2019-dataset/time_series_covid_19_recovered.csv
/kaggle/input/novel-corona-virus-2019-dataset/covid_19_data.csv
/kaggle/input/novel-corona-virus-2019-dataset/time_series_covid_19_deaths.csv
/kaggle/input/novel-corona-virus-2019-dataset/COVID19_line_list_data.csv
/kaggle/input/novel-corona-virus-2019-dataset/COVID19_open_line_list.csv
/kaggle/input/coronavirusdataset/TimeProvince.csv
/kaggle/input/coronavirusdataset/PatientInfo.csv
/kaggle/input/coronavirusdataset/Time.csv
/kaggle/input/coronavirusdataset/Weather.csv
/kaggle/input/coronavirusdataset/Region.csv
/kaggle/input/coronavirusdataset/TimeAge.csv
/kaggle/input/coronavirusdataset/TimeGender.csv
/kaggle/input/coronavirusdataset/Policy.csv
/kaggle/input/coro

In [2]:
patient = pd.read_csv('/kaggle/input/coronavirusdataset/PatientInfo.csv')
route = pd.read_csv('/kaggle/input/coronavirusdataset/PatientRoute.csv')
region = pd.read_csv('/kaggle/input/coronavirusdataset/Region.csv')

In [3]:
patient.head()

patient_id  global_num     sex birth_year  age country province  \
0  1000000001         2.0    male       1964  50s   Korea    Seoul   
1  1000000002         5.0    male       1987  30s   Korea    Seoul   
2  1000000003         6.0    male       1964  50s   Korea    Seoul   
3  1000000004         7.0    male       1991  20s   Korea    Seoul   
4  1000000005         9.0  female       1992  20s   Korea    Seoul   

          city disease        infection_case  infection_order infected_by  \
0   Gangseo-gu     NaN       overseas inflow              1.0         NaN   
1  Jungnang-gu     NaN       overseas inflow              1.0         NaN   
2    Jongno-gu     NaN  contact with patient              2.0  2002000001   
3      Mapo-gu     NaN       overseas inflow              1.0         NaN   
4  Seongbuk-gu     NaN  contact with patient              2.0  1000000002   

  contact_number symptom_onset_date confirmed_date released_date  \
0             75         2020-01-22     2020-01-23    2020-02-05   
1             31                NaN     2020-01-30    2020-03-02   
2             17                NaN     2020-01-30    2020-02-19   
3              9         2020-01-26     2020-01-30    2020-02-15   
4              2                NaN     2020-01-31    2020-02-24   

  deceased_date     state  
0           NaN  released  
1           NaN  released  
2           NaN  released  
3           NaN  released  
4           NaN  released

In [4]:
region.head()

code province         city   latitude   longitude  \
0  10000    Seoul        Seoul  37.566953  126.977977   
1  10010    Seoul   Gangnam-gu  37.518421  127.047222   
2  10020    Seoul  Gangdong-gu  37.530492  127.123837   
3  10030    Seoul   Gangbuk-gu  37.639938  127.025508   
4  10040    Seoul   Gangseo-gu  37.551166  126.849506   

   elementary_school_count  kindergarten_count  university_count  \
0                      607                 830                48   
1                       33                  38                 0   
2                       27                  32                 0   
3                       14                  21                 0   
4                       36                  56                 1   

   academy_ratio  elderly_population_ratio  elderly_alone_ratio  \
0           1.44                     15.38                  5.8   
1           4.18                     13.17                  4.3   
2           1.54                     14.55                  5.4   
3           0.67                     19.49                  8.5   
4           1.17                     14.39                  5.7   

   nursing_home_count  
0               22739  
1                3088  
2                1023  
3                 628  
4                1080

# 1. plotting just a map 
제일 먼저, 그냥 지도 띄우기

```python
folium.Map([37,128]. zoom_start = 7, *tiles='Stamen Terrain'*)
folium.Map([37,128]. zoom_start = 7, *tiles='Stamen Toner'*)
```
There are several types of map, default, Stamen Terrain, and Stamen Toner. 

I prefer default option. 

In [5]:
m = folium.Map([36, 128], zoom_start=7) 

# you can try these options
# m = folium.Map([37, 128], zoom_start=7, tiles='Stamen Terrain') 
# m = folium.Map([37, 128], zoom_start=7, tiles='Stamen Toner') 

m

### Additional tool : Fullscreen, MousePosition(get coordinates)
추가 기능 : 풀스크린으로 만들기, 마우스 갖다대면 좌표 뜨게 하기

In [6]:
m = folium.Map([36, 128], zoom_start=7) 

plugins.Fullscreen(position='topright',  # Full screen
                   title='Click to Expand', 
                   title_cancel='Click to Exit', 
                   force_separate_button=True).add_to(m)

plugins.MousePosition().add_to(m) ## you can easily get coordinates.


m

# 2. MarkerCluster : Lets see the number of regional confirmed patient.
지역별로 몇명의 확진환자가 나왔는지 한번 봐볼까요?

In [7]:
regional_patient = pd.merge(patient[['patient_id','confirmed_date','sex','age','province','city']],region[['province','city','latitude','longitude']], how = 'left', on = ['province','city'])
display(regional_patient.head())
print('There are a few missing values')
print('약간의 missing 값들이 있네요. 분석할 때 유의해야할 것 같습니다.')
display(regional_patient.isnull().sum() / regional_patient.shape[0])

patient_id confirmed_date     sex  age province         city   latitude  \
0  1000000001     2020-01-23    male  50s    Seoul   Gangseo-gu  37.551166   
1  1000000002     2020-01-30    male  30s    Seoul  Jungnang-gu  37.606832   
2  1000000003     2020-01-30    male  50s    Seoul    Jongno-gu  37.572999   
3  1000000004     2020-01-30    male  20s    Seoul      Mapo-gu  37.566283   
4  1000000005     2020-01-31  female  20s    Seoul  Seongbuk-gu  37.589562   

    longitude  
0  126.849506  
1  127.092656  
2  126.979189  
3  126.901644  
4  127.016700

There are a few missing values
약간의 missing 값들이 있네요. 분석할 때 유의해야할 것 같습니다.


patient_id        0.000000
confirmed_date    0.000749
sex               0.082418
age               0.119630
province          0.000000
city              0.019481
latitude          0.037962
longitude         0.037962
dtype: float64

### Captial Area(value of 724), including Seoul, Gyeonggi-do, Incheon etc., Gyeongsangbuk-do(972) look serious.

서울 경기 인천 지역, 즉 수도권 지역과, 경북지역의 감염자수가 가장 높은 것을 알 수 있습니다.

In [8]:
regional_count = regional_patient[['latitude','longitude']].dropna() # drop missing values

m = folium.Map([36, 128], zoom_start=7)

plugins.MousePosition().add_to(m) 

plugins.MarkerCluster(regional_count).add_to(m)

m

# 3. Make subgroups to plot : Female / Male
여성, 남성 감염자를 하위그룹으로 하여 따로따로 볼 수 있도록 지도를 그려보겠습니다


In [9]:
male_patient = regional_patient\
.query('sex in ("male")')[['latitude','longitude']].dropna()

female_patient = regional_patient\
.query('sex in ("female")')[['latitude','longitude']].dropna()


m = folium.Map([36, 128], zoom_start=7) 

initial = folium.plugins.MarkerCluster(control=False)

m.add_child(initial)


female_g = plugins.FeatureGroupSubGroup(initial, 'Female')
m.add_child(female_g)

male_g = plugins.FeatureGroupSubGroup(initial, 'Male') 
m.add_child(male_g)


plugins.MarkerCluster(female_patient).add_to(female_g)

plugins.MarkerCluster(male_patient).add_to(male_g)



folium.LayerControl(collapsed=False).add_to(m)

m

# 4. Make a Heat map : Instead of the number

지역별로 얼마나 많은 감염자가 있는지, 숫자로 보는 것이 아닌, heat map을 활용하여 시각적으로 나타내보겠습니다

**Heatmap parameter**

```python
folium.plugins.HeatMap(data, name=None, min_opacity=0.5, 
                       max_zoom=18, max_val=1.0, radius=25, blur=15, 
                       gradient=None, overlay=True, control=True, show=True, **kwargs)
```

```
- min_opacity (default 1.) – The minimum opacity the heat will start at.
- max_zoom (default 18) – Zoom level where the points reach maximum intensity (as intensity scales with zoom), equals maxZoom of the map by default
- max_val (float, default 1.) – Maximum point intensity
- radius (int, default 25) – Radius of each “point” of the heatmap
- blur (int, default 15) – Amount of blur
- gradient (dict, default None) – Color gradient config. e.g. {0.4: ‘blue’, 0.65: ‘lime’, 1: ‘red’}
- overlay (bool, default True) – Adds the layer as an optional overlay (True) or the base layer (False).
- control (bool, default True) – Whether the Layer will be included in LayerControls.
- show (bool, default True) – Whether the layer will be shown on opening (only for overlays).
```

[Link](https://python-visualization.github.io/folium/plugins.html)


In [10]:
heat_data = regional_patient\
.groupby(['latitude','longitude'])['patient_id'].count().reset_index()\
.values\
.tolist()

m = folium.Map([36, 128], zoom_start=7)#, tiles = 'stamentoner')

folium.plugins.HeatMap(heat_data).add_to(m)

m

### In my opinion, I prefer Heatmap to MarkCluster. How about you? :-)
저 개인적으로는 히트맵이 보기 좋네요 여러분들은 어떠신가요? ㅎㅎㅎ

### Additional try : MarkCluster Layer On the Heatmap Layer.

Sometimes, we need to plot several statistics on only one map.(Multivariate)

So i tried it with Heatmap and MarkCluster.

가끔 지도 위에 여러개의 통계량을 나타내야할 때가 있는데요, Heatmap과 MarkCluster로 시도해봤습니다


In [11]:
heat_data = region[['latitude','longitude','nursing_home_count']].values.tolist() # nursing home count 

mark_data = regional_patient[['latitude','longitude']].dropna() # drop missing values

m = folium.Map([36, 128], zoom_start=7)

plugins.MarkerCluster(mark_data).add_to(m) # Layer 1

folium.plugins.HeatMap(heat_data, max_opacity = 0.3).add_to(m) # Layer 2

m

### Doesn't look good. 

보기 좋진 않네요.

# 5. Heatmap with time : time series heat map

```python
folium.plugins.HeatMapWithTime(data, index=None, name=None, 
                               radius=15, min_opacity=0, max_opacity=0.6, 
                               scale_radius=False, gradient=None, 
                               use_local_extrema=False, auto_play=False, 
                               display_index=True, index_steps=1, min_speed=0.1, 
                               max_speed=10, speed_step=0.1, position='bottomleft', 
                               overlay=True, control=True, show=True)
```

**Parameter** what i find important
```
data – The points you want to plot. The outer list corresponds to the various time steps in sequential order. (weight is in (0, 1] range and defaults to 1 if not specified for a point)

index  – the same length as data, or is replaced by a simple count if not specified.

radius (default 15.) – The radius used around points for the heatmap.

min_opacity (default 0) – The minimum opacity for the heatmap.

max_opacity (default 0.6) – The maximum opacity for the heatmap.

scale_radius (default False) – Scale the radius of the points based on the zoom level.

auto_play (default False) – Automatically play the animation across time.
```

[More](https://python-visualization.github.io/folium/plugins.html)

In [12]:
#prepare data

regional_patient_bytime = regional_patient\
.groupby(['confirmed_date','latitude','longitude'])['patient_id'].count().reset_index()\
.sort_values(by = 'confirmed_date')

date_rng = pd.date_range(regional_patient_bytime['confirmed_date'].min(), regional_patient_bytime['confirmed_date'].max())
date_rng = [str(i)[:10] for i in date_rng]

all_date_region = pd.DataFrame({'confirmed_date' : np.repeat(date_rng,region[['latitude','longitude']].drop_duplicates().shape[0]),
              'latitude' : np.tile(list(region['latitude'].drop_duplicates()), len(date_rng)),
              'longitude' : np.tile(list(region['longitude'].drop_duplicates()), len(date_rng))})

all_date_region = pd.merge(all_date_region, regional_patient_bytime, on = ['confirmed_date','latitude','longitude'], how = 'left').fillna(0)
all_date_region['cumsum'] = all_date_region.groupby(['latitude','longitude'])['patient_id'].cumsum()

all_date_region = all_date_region[all_date_region['cumsum'] != 0]

time_index, data = [], []

for date in all_date_region['confirmed_date'].unique():
    time_index += [date[6:].replace('-','/')]
    temp_list = all_date_region.query('confirmed_date == @date')[['latitude','longitude','cumsum']].values.tolist()
    data += [temp_list]
    del temp_list

### HeatMapWithTime needs this type of input data.


In [13]:
data[:5], time_index[:5]

([[[37.551165999999995, 126.849506, 1.0]],
  [[37.551165999999995, 126.849506, 1.0]],
  [[37.551165999999995, 126.849506, 1.0]],
  [[37.551165999999995, 126.849506, 1.0], [37.658363, 126.831961, 1.0]],
  [[37.551165999999995, 126.849506, 1.0],
   [37.658363, 126.831961, 1.0],
   [36.992293, 127.11270900000001, 1.0]]],
 ['1/23', '1/24', '1/25', '1/26', '1/27'])

In [14]:
# make a map
    
m = folium.Map([36, 128], zoom_start=7)#, tiles = 'Mapbox Bright')

hm = folium.plugins.HeatMapWithTime(data, index=time_index, auto_play=False, min_opacity=0.3, radius = 25, )

hm.add_to(m)

for bottom, click in zip([60,90,120,150,180],['Loop','Forward','Play','Reverse','Backward']):
    
    # Thank you for html code. https://www.kaggle.com/poonsfc5/ds4c-covid-19-in-korea-eda-with-geo-data
    name = '''
            <div style="position: fixed; bottom: '''+str(bottom)+'''px; left: 50px; width: 100px; height: 29px; 
                        background-color: white; border:1px solid grey; z-index:9999; font-size:11px;text-align:center;"
                        >&nbsp; <br><b>Click : '''+ click +'''</b></div>'''  

    m.get_root().html.add_child(folium.Element(name))

m

# 6. Make Circles with timebar : Timestamped Geojson

```python
TimestampedGeoJson(data, transition_time=200, loop=True, auto_play=True, 
                   add_last_point=True, period='P1D', min_speed=0.1, max_speed=10, 
                   loop_button=False, date_options='YYYY-MM-DD HH:mm:ss', 
                   time_slider_drag_update=False, duration=None)
```

parameter i find important
```
period (str, default "P1D") –  ‘P1M’ 1/month, ‘P1D’ 1/day, ‘PT1H’ 1/hour, and ‘PT1M’ 1/minute
```

[more](https://python-visualization.github.io/folium/plugins.html)

In [15]:
# prepare data
df_dropna = regional_patient.dropna()
df_dropna['timestamp'] = [i+'T00:00:00' for i in df_dropna['confirmed_date']]

points = []
for date in sorted(df_dropna['confirmed_date'].unique()):
    temp = df_dropna.query('confirmed_date == @date')
    
    temp_dict = {}
    temp_dict['coordinates'] = temp[['longitude','latitude']].values.tolist()
    temp_dict['dates'] = temp['timestamp'].values.tolist()
    
    points += [temp_dict]

features = [ { 'type': 'Feature', 
                  'geometry': { 'type': 'MultiPoint', 
                               'coordinates': point['coordinates'], }, 
                  'properties': { 'times': point['dates'],
                                 'icon' : 'circle'}
             } for point in points ] 

### TimestampedGeoJson needs this type of input data.

In [16]:
features[:3]

[{'type': 'Feature',
  'geometry': {'type': 'MultiPoint',
   'coordinates': [[126.849506, 37.551165999999995]]},
  'properties': {'times': ['2020-01-23T00:00:00'], 'icon': 'circle'}},
 {'type': 'Feature',
  'geometry': {'type': 'MultiPoint', 'coordinates': [[126.831961, 37.658363]]},
  'properties': {'times': ['2020-01-26T00:00:00'], 'icon': 'circle'}},
 {'type': 'Feature',
  'geometry': {'type': 'MultiPoint',
   'coordinates': [[127.11270900000001, 36.992293]]},
  'properties': {'times': ['2020-01-27T00:00:00'], 'icon': 'circle'}}]

In [17]:
m = folium.Map( location=[36, 128], zoom_start=7 )

plugins.TimestampedGeoJson({ 
    'type': 'FeatureCollection', 
    'features': features, 
}, period='P1D', auto_play = False).add_to(m)

m

### Pydeck to be continued!

# Thank you for attention!!

